In [8]:
import simpy 
class School: 
 def __init__(self, env): 
   self.env = env 
   self.class_ends = env.event() 
   self.pupil_procs = [env.process(self.pupil()) for i in range(3)] 
   self.bell_proc = env.process(self.bell()) 
  
 def bell(self): 
   for i in range(4): 
     yield self.env.timeout(45) 
     self.class_ends.succeed() 
     self.class_ends = self.env.event() 
     print("\n_звонок_", i+1,"::",env.now) 
 
 def pupil(self): 
   for i in range(3): 
    yield self.class_ends 
    print('|o/', end=' ') 
 
env = simpy.Environment() 
school = School(env) 
env.run()


_звонок_ 1 :: 45
|o/ |o/ |o/ 
_звонок_ 2 :: 90
|o/ |o/ |o/ 
_звонок_ 3 :: 135
|o/ |o/ |o/ 
_звонок_ 4 :: 180


In [10]:
import simpy
from simpy.events import AnyOf, AllOf, Event

def test_condition(env):
  t1, t2 = env.timeout(1, value='вкл'), env.timeout(2, value='выкл')
  ret = yield t1 | t2
  #assert ret == {t1: 'вкл'}

  t1, t2 = env.timeout(1, value='вкл'), env.timeout(2, value='выкл')
  ret = yield t1 & t2
  #assert ret == {t1: 'вкл', t2: 'выкл'}

  # можно использовать операторы & и |
  e1, e2, e3 = [env.timeout(i) for i in range(3)]
  yield (e1 | e2) & e3
  #assert all(e.triggered for e in [e1, e2, e3])
  print(t1, t2, e1, e2, e3)

env = simpy.Environment()
proc = env.process(test_condition(env))
env.run()


<Timeout(1, value=вкл) object at 0x233ee7a94c0> <Timeout(2, value=выкл) object at 0x233ee7a8c80> <Timeout(0) object at 0x233ee762bd0> <Timeout(1) object at 0x233ee7a9610> <Timeout(2) object at 0x233ee7a9f70>


In [11]:
import simpy

def my_proc(env):
    yield env.timeout(1)
    return 'Python & Anaconda'

env = simpy.Environment()
proc = env.process(my_proc(env))
env.run(until=proc)
print(proc.value)

Python & Anaconda


In [12]:
class GasStation: 
   def __init__(self, env): 
      self.fuel_dispensers = simpy.Resource(env, capacity=2) 
      self.gas_tank = simpy.Container(env, init=100, capacity=1000) 
      self.mon_proc = env.process(self.monitor_tank(env)) 
    
   def monitor_tank(self, env): 
      while True: 
         if self.gas_tank.level < 100: 
            print(f'Вызов заправщика в {env.now}') 
            env.process(tanker(env, self)) 
         yield env.timeout(15) 

    
def tanker(env, gas_station): 
    yield env.timeout(10) # заправщику надо ехать 10 мин 
    print(f'Заправщик приехал в {env.now}')
    amount = gas_station.gas_tank.capacity - gas_station.gas_tank.level
    yield gas_station.gas_tank.put(amount) 
    
def car(name, env, gas_station):
    print(f'Клиент {name} приехал в {env.now}') 
    with gas_station.fuel_dispensers.request() as req: 
       yield req 
       print(f'Клиент {name} начал заправку в {env.now}') 
       yield gas_station.gas_tank.get(40) 
       yield env.timeout(5) 
       print(f'Клиент {name} закончил заправку в {env.now}') 
    
def car_generator(env, gas_station): 
    for i in range(4): 
       env.process(car(i, env, gas_station)) 
       yield env.timeout(5) 
    
env = simpy.Environment() 
gas_station = GasStation(env) 
car_gen = env.process(car_generator(env, gas_station)) 
env.run(35)


Клиент 0 приехал в 0
Клиент 0 начал заправку в 0
Клиент 1 приехал в 5
Клиент 0 закончил заправку в 5
Клиент 1 начал заправку в 5
Клиент 2 приехал в 10
Клиент 1 закончил заправку в 10
Клиент 2 начал заправку в 10
Вызов заправщика в 15
Клиент 3 приехал в 15
Клиент 3 начал заправку в 15
Заправщик приехал в 25
Клиент 2 закончил заправку в 30
Клиент 3 закончил заправку в 30


In [14]:
env = simpy.Environment()
issues = simpy.PriorityStore(env)

def inspector(env, issues):
    for issue in [simpy.PriorityItem('P2', '#0000'),
          simpy.PriorityItem('P0', '#0001'),
          simpy.PriorityItem('P3', '#0002'),
          simpy.PriorityItem('P1', '#0003')]:
       yield env.timeout(1)
       print(env.now, 'проверил', issue)
       yield issues.put(issue)

def maintainer(env, issues):
    while True:
       yield env.timeout(3)
       issue = yield issues.get()
       print(env.now, 'починил', issue)

_ = env.process(inspector(env, issues))
_ = env.process(maintainer(env, issues))
env.run()


1 проверил PriorityItem(priority='P2', item='#0000')
2 проверил PriorityItem(priority='P0', item='#0001')
3 проверил PriorityItem(priority='P3', item='#0002')
3 починил PriorityItem(priority='P0', item='#0001')
4 проверил PriorityItem(priority='P1', item='#0003')
6 починил PriorityItem(priority='P1', item='#0003')
9 починил PriorityItem(priority='P2', item='#0000')
12 починил PriorityItem(priority='P3', item='#0002')


In [20]:
from collections import namedtuple

Machine = namedtuple('Станок', 'size, duration')
m1 = Machine(1, 2)  # малый и медленный станок
m2 = Machine(2, 1)  # большой и быстрый станок
env = simpy.Environment()
machine_shop = simpy.FilterStore(env, capacity=2)
machine_shop.items = [m1, m2]  # собираем цех из станков

def user(name, env, ms, size):
   machine = yield ms.get(lambda machine: machine.size == size)
   print(name, 'получил', machine, 'в', env.now)
   yield env.timeout(machine.duration)
   yield ms.put(machine)
   print(name, 'освободил', machine, 'в', env.now)

users =[env.process(user(str(i+1)+'й',env,machine_shop,(i%2)+1)) for i in range(4)]
env.run()


1й получил Станок(size=1, duration=2) в 0
2й получил Станок(size=2, duration=1) в 0
2й освободил Станок(size=2, duration=1) в 1
4й получил Станок(size=2, duration=1) в 1
1й освободил Станок(size=1, duration=2) в 2
4й освободил Станок(size=2, duration=1) в 2
3й получил Станок(size=1, duration=2) в 2
3й освободил Станок(size=1, duration=2) в 4


In [27]:
def user(name, env, res, prio, preempt):
    with res.request(priority=prio, preempt=preempt) as req:
       try:
          print(f'{name} запрос в {env.now}')
          assert isinstance(env.now, int), type(env.now)
          yield req
          assert isinstance(env.now, int), type(env.now)
          print(f'{name} получил ресурс в {env.now}')
          yield env.timeout(3)
       except simpy.Interrupt: 
          print(f'{name} был прерван в {env.now}')

env = simpy.Environment()
res = simpy.PreemptiveResource(env, capacity=1)
A = env.process(user('A', env, res, prio=0, preempt=True))
B = env.process(user('B', env, res, prio=-2, preempt=False))
C = env.process(user('C', env, res, prio=-1, preempt=True))

env.run(until=9)

A запрос в 0
B запрос в 0
C запрос в 0
A получил ресурс в 0
B получил ресурс в 3
C получил ресурс в 6


In [28]:
def resource_user(name, env, resource, wait, prio): 
   yield env.timeout(wait) 
   with resource.request(priority=prio) as req: 
      print(f'{name} запрос в {env.now} с приоритетом={prio}')
      yield req 
      print(f'{name} получил ресурс в {env.now}')
      try:
         yield env.timeout(3)
      except simpy.Interrupt as interrupt:
         by = interrupt.cause.by
         usage = env.now - interrupt.cause.usage_since
         print(f'{name} был прерван {by} в {env.now} после {usage}')

env = simpy.Environment()
res = simpy.PreemptiveResource(env, capacity=1) 
p1 = env.process(resource_user(1, env, res, wait=0, prio=0)) 
p2 = env.process(resource_user(2, env, res, wait=1, prio=0)) 
p3 = env.process(resource_user(3, env, res, wait=2, prio=-1)) 
env.run() 


1 запрос в 0 с приоритетом=0
1 получил ресурс в 0
2 запрос в 1 с приоритетом=0
3 запрос в 2 с приоритетом=-1
1 был прерван <Process(resource_user) object at 0x233ef2f0b00> в 2 после 2
3 получил ресурс в 2
2 получил ресурс в 5


In [29]:
def resource_user(name, env, resource, wait, prio):
     yield env.timeout(wait)
     with resource.request(priority=prio) as req:
         print(f'{name} запрос в {env.now} с приоритетом={prio}')
         yield req
         print(f'{name} получил ресурс в {env.now}')
         yield env.timeout(3)

env = simpy.Environment()
res = simpy.PriorityResource(env, capacity=1)
p1 = env.process(resource_user(1, env, res, wait=0, prio=0))
p2 = env.process(resource_user(2, env, res, wait=1, prio=0))
p3 = env.process(resource_user(3, env, res, wait=2, prio=-1))
env.run()


1 запрос в 0 с приоритетом=0
1 получил ресурс в 0
2 запрос в 1 с приоритетом=0
3 запрос в 2 с приоритетом=-1
3 получил ресурс в 3
2 получил ресурс в 6


In [32]:
import simpy
def car1(env, name, bcs, driving_time, charge_duration):
    # Моделирование ЭЗС
    yield env.timeout(driving_time)
    # Запрос одной из зарядок
    print(f'{name} прибыл в {env.now}')
    with bcs.request() as req:
        yield req
    # Зарядка
    print(f'{name} начал зарядку в {env.now}')
    yield env.timeout(charge_duration)
    print(f'{name} покинул ЭЗС в {env.now}')

env = simpy.Environment()
bcs = simpy.Resource(env, capacity=2)

for i in range(4):
    env.process(car1(env, 'Электромобиль %d' % i, bcs, i*2, 5))
env.run()

Электромобиль 0 прибыл в 0
Электромобиль 0 начал зарядку в 0
Электромобиль 1 прибыл в 2
Электромобиль 1 начал зарядку в 2
Электромобиль 2 прибыл в 4
Электромобиль 2 начал зарядку в 4
Электромобиль 0 покинул ЭЗС в 5
Электромобиль 3 прибыл в 6
Электромобиль 3 начал зарядку в 6
Электромобиль 1 покинул ЭЗС в 7
Электромобиль 2 покинул ЭЗС в 9
Электромобиль 3 покинул ЭЗС в 11


In [34]:
class Car(object):
    def __init__(self, env):
       self.env = env
       self.action = env.process(self.run())
    def run(self):
        while True:
           print(f'Начало парковки и зарядки в {self.env.now}')
           charge_duration = 5
           # Можно прервать зарядку
           try:
              yield self.env.process(self.charge(charge_duration))
           except simpy.Interrupt:
               # Прерываем зарядку и начинаем движение
               print('Зарядка прервана')
           print(f'Начало движения в {self.env.now}')
           trip_duration = 2
           yield self.env.timeout(trip_duration)

    def charge(self, duration):
        yield self.env.timeout(duration)

def driver(env, car):
   yield env.timeout(3)
   car.action.interrupt()

env = simpy.Environment()
car = Car(env)
env.process(driver(env, car))
env.run(until=15)


Начало парковки и зарядки в 0
Зарядка прервана
Начало движения в 3
Начало парковки и зарядки в 5
Начало движения в 10
Начало парковки и зарядки в 12
